In [1]:
import os, sys
sys.path.append(os.path.abspath('../'))
import pandas as pd
from datetime import datetime
from EMAWorkbench import Policy
from EMAWorkbench.em_framework import sample_uncertainties
from EMAWorkbench import SequentialEvaluator, ema_logging, save_results


def evaluation(model, problem, random_seed, steps, policy_path, result_path, real_num=False):
    the_model, _ = model(problem=problem, random_seed=random_seed)

    ea_policies = pd.read_csv(policy_path)
    policies = []
    for index, row in ea_policies.iterrows():
        if real_num:
            policy = Policy(str(index), **{str(i):row[str(i)] for i in range(steps)})
        else:
            policy = Policy(str(index), **{str(i):int(row[str(i)]) for i in range(steps)})
        policies.append(policy)
        
    ema_logging.log_to_stderr(ema_logging.INFO)
    current_time = datetime.now().strftime("-%d-%m-%Y-%H-%M")

    i = 0
    for policy in policies:
        with SequentialEvaluator(the_model) as evaluator:
            results = evaluator.perform_experiments(policies=policy)

        save_results(results, result_path+f'{current_time}_{i}.tar.gz')
        i += 1
    return results

In [2]:
import os, sys
sys.path.append(os.path.abspath('../'))
import pandas as pd
from datetime import datetime
from EMAWorkbench import Policy
from EMAWorkbench.em_framework import sample_uncertainties
from EMAWorkbench import SequentialEvaluator, ema_logging, save_results


def robustness_evaluation(model, problem, random_seed, steps, scenarios_num, 
                          scenario_path, policy_path, result_path, real_num=False):
    the_model, _ = model(problem=problem, random_seed=random_seed)
    
    evaluation_df_read = pd.read_csv(scenario_path)
    evaluation_scenarios_designs = list(evaluation_df_read.to_records(index=False))
    evaluation_scenarios = sample_uncertainties(the_model, scenarios_num)
    evaluation_scenarios.designs = evaluation_scenarios_designs

    ea_policies = pd.read_csv(policy_path)
    policies = []
    for index, row in ea_policies.iterrows():
        if real_num:
            policy = Policy(str(index), **{str(i):row[str(i)] for i in range(steps)})
        else:
            policy = Policy(str(index), **{str(i):int(row[str(i)]) for i in range(steps)})
        policies.append(policy)
        
    ema_logging.log_to_stderr(ema_logging.INFO)
    current_time = datetime.now().strftime("-%d-%m-%Y-%H-%M")

    i = 0
    for policy in policies:
        with SequentialEvaluator(the_model) as evaluator:
            results = evaluator.perform_experiments(scenarios=evaluation_scenarios, policies=policy)

        save_results(results, result_path+f'{current_time}_{i}.tar.gz')
        i += 1
    return results

# Discrete Dam Problem

In [ ]:
from models.ema_dam1 import dam_problem1
from utils.ea.create_models import create_dam_discrete_testing


evaluation(model=create_dam_discrete_testing, problem=dam_problem1, random_seed=1793476144, steps=100,
           policy_path='../results/ea_dam/discrete_1-12-06-2022-05-25_policy.csv',
           result_path=f'../results/dam_discrete_performance/ea')

ImportError: cannot import name 'create_dam_discrete_testing' from 'utils.ea.create_models' (/Users/zppei/Documents/PhD-Project/code/Evolutionary/utils/ea/create_models.py)

# Robust Dam Problem (random initial state)

In [3]:
from models.ema_dam_uncertain1 import dam_uncertain_problem1
from utils.ea.create_models import create_dam_robust_training


robustness_evaluation(model=create_dam_robust_training, problem=dam_uncertain_problem1, 
                      random_seed=1793476144, steps=100, scenarios_num=1000,
                      scenario_path="../results/dam_scenarios/evaluation_scenarios.csv",
                      policy_path='../results/ea_dam_robust/2_1-03-07-2022-06-48_policy.csv',
                      result_path=f'../results/dam_robust_performance_5/ea')

[MainProcess/INFO] performing 1000 scenarios * 1 policies * 1 model(s) = 1000 experiments
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.p

(         s_init    0    1    2    3    4    5    6    7    8  ...   93   94  \
 0    155.321773  5.0  6.0  5.0  5.0  5.0  5.0  7.0  5.0  7.0  ...  5.0  9.0   
 1    126.723411  5.0  6.0  5.0  5.0  5.0  5.0  7.0  5.0  7.0  ...  5.0  9.0   
 2    136.122819  5.0  6.0  5.0  5.0  5.0  5.0  7.0  5.0  7.0  ...  5.0  9.0   
 3    164.708120  5.0  6.0  5.0  5.0  5.0  5.0  7.0  5.0  7.0  ...  5.0  9.0   
 4    165.943724  5.0  6.0  5.0  5.0  5.0  5.0  7.0  5.0  7.0  ...  5.0  9.0   
 ..          ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
 995  199.910831  5.0  6.0  5.0  5.0  5.0  5.0  7.0  5.0  7.0  ...  5.0  9.0   
 996  131.942802  5.0  6.0  5.0  5.0  5.0  5.0  7.0  5.0  7.0  ...  5.0  9.0   
 997  176.601969  5.0  6.0  5.0  5.0  5.0  5.0  7.0  5.0  7.0  ...  5.0  9.0   
 998  129.312759  5.0  6.0  5.0  5.0  5.0  5.0  7.0  5.0  7.0  ...  5.0  9.0   
 999  159.885022  5.0  6.0  5.0  5.0  5.0  5.0  7.0  5.0  7.0  ...  5.0  9.0   
 
       95   96   97   98   99  scenari

In [4]:
from models.ema_dam_uncertain1 import dam_uncertain_problem1
from utils.ea.create_models import create_dam_robust_training


robustness_evaluation(model=create_dam_robust_training, problem=dam_uncertain_problem1, 
                      random_seed=1793476144, steps=100, scenarios_num=1000,
                      scenario_path="../results/dam_scenarios/evaluation_scenarios.csv",
                      policy_path='../results/ea_dam_robust/mv_2_1-03-07-2022-07-14_policy.csv',
                      result_path=f'../results/dam_robust_performance_5/ea_mv')

[MainProcess/INFO] performing 1000 scenarios * 1 policies * 1 model(s) = 1000 experiments
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.p

(         s_init     0    1    2    3    4     5    6    7    8  ...   93   94  \
 0    155.321773  10.0  9.0  5.0  5.0  6.0  10.0  5.0  5.0  5.0  ...  5.0  6.0   
 1    126.723411  10.0  9.0  5.0  5.0  6.0  10.0  5.0  5.0  5.0  ...  5.0  6.0   
 2    136.122819  10.0  9.0  5.0  5.0  6.0  10.0  5.0  5.0  5.0  ...  5.0  6.0   
 3    164.708120  10.0  9.0  5.0  5.0  6.0  10.0  5.0  5.0  5.0  ...  5.0  6.0   
 4    165.943724  10.0  9.0  5.0  5.0  6.0  10.0  5.0  5.0  5.0  ...  5.0  6.0   
 ..          ...   ...  ...  ...  ...  ...   ...  ...  ...  ...  ...  ...  ...   
 995  199.910831  10.0  9.0  5.0  5.0  6.0  10.0  5.0  5.0  5.0  ...  5.0  6.0   
 996  131.942802  10.0  9.0  5.0  5.0  6.0  10.0  5.0  5.0  5.0  ...  5.0  6.0   
 997  176.601969  10.0  9.0  5.0  5.0  6.0  10.0  5.0  5.0  5.0  ...  5.0  6.0   
 998  129.312759  10.0  9.0  5.0  5.0  6.0  10.0  5.0  5.0  5.0  ...  5.0  6.0   
 999  159.885022  10.0  9.0  5.0  5.0  6.0  10.0  5.0  5.0  5.0  ...  5.0  6.0   
 
       95   96

In [3]:
from models.ema_dam_uncertain1 import dam_uncertain_problem1
from utils.ea.create_models import create_dam_robust_training


robustness_evaluation(model=create_dam_robust_training, problem=dam_uncertain_problem1, 
                      random_seed=1793476144, steps=100, scenarios_num=1000,
                      scenario_path="../results/dam_scenarios/evaluation_scenarios.csv",
                      policy_path='../results/ea_dam_robust/avg_2_1-06-07-2022-05-32_policy.csv',
                      result_path=f'../results/dam_robust_performance_5/ea_avg')

[MainProcess/INFO] performing 1000 scenarios * 1 policies * 1 model(s) = 1000 experiments
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.p

(         s_init     0     1     2    3    4    5    6    7    8  ...   93  \
 0    155.321773  10.0  10.0  10.0  5.0  5.0  5.0  6.0  5.0  5.0  ...  4.0   
 1    126.723411  10.0  10.0  10.0  5.0  5.0  5.0  6.0  5.0  5.0  ...  4.0   
 2    136.122819  10.0  10.0  10.0  5.0  5.0  5.0  6.0  5.0  5.0  ...  4.0   
 3    164.708120  10.0  10.0  10.0  5.0  5.0  5.0  6.0  5.0  5.0  ...  4.0   
 4    165.943724  10.0  10.0  10.0  5.0  5.0  5.0  6.0  5.0  5.0  ...  4.0   
 ..          ...   ...   ...   ...  ...  ...  ...  ...  ...  ...  ...  ...   
 995  199.910831  10.0  10.0  10.0  5.0  5.0  5.0  6.0  5.0  5.0  ...  4.0   
 996  131.942802  10.0  10.0  10.0  5.0  5.0  5.0  6.0  5.0  5.0  ...  4.0   
 997  176.601969  10.0  10.0  10.0  5.0  5.0  5.0  6.0  5.0  5.0  ...  4.0   
 998  129.312759  10.0  10.0  10.0  5.0  5.0  5.0  6.0  5.0  5.0  ...  4.0   
 999  159.885022  10.0  10.0  10.0  5.0  5.0  5.0  6.0  5.0  5.0  ...  4.0   
 
       94   95   96   97   98   99  scenario  policy          

# Robust Dam Problem (random inflow)

In [4]:
from models.ema_dam_uncertain1 import dam_uncertain_problem1
from utils.ea.create_models import create_dam_robust_training


robustness_evaluation(model=create_dam_robust_training, problem=dam_uncertain_problem1, 
                      random_seed=1793476144, steps=100, scenarios_num=1000,
                      scenario_path="../results/dam_scenarios/evaluation_scenarios_random_inflow.csv",
                      policy_path='../results/ea_dam_robust/random_inflow_1-12-06-2022-13-02_policy.csv',
                      result_path=f'../results/dam_robust_performance/ea_random_inflow')

[MainProcess/INFO] performing 1000 scenarios * 1 policies * 1 model(s) = 1000 experiments
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.p

(     s_init_idx    0    1    2    3    4    5    6    7    8  ...   93   94  \
 0           0.0  6.0  5.0  6.0  5.0  7.0  5.0  5.0  6.0  8.0  ...  5.0  6.0   
 1           0.0  6.0  5.0  6.0  5.0  7.0  5.0  5.0  6.0  8.0  ...  5.0  6.0   
 2           0.0  6.0  5.0  6.0  5.0  7.0  5.0  5.0  6.0  8.0  ...  5.0  6.0   
 3           0.0  6.0  5.0  6.0  5.0  7.0  5.0  5.0  6.0  8.0  ...  5.0  6.0   
 4           0.0  6.0  5.0  6.0  5.0  7.0  5.0  5.0  6.0  8.0  ...  5.0  6.0   
 ..          ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
 995         0.0  6.0  5.0  6.0  5.0  7.0  5.0  5.0  6.0  8.0  ...  5.0  6.0   
 996         0.0  6.0  5.0  6.0  5.0  7.0  5.0  5.0  6.0  8.0  ...  5.0  6.0   
 997         0.0  6.0  5.0  6.0  5.0  7.0  5.0  5.0  6.0  8.0  ...  5.0  6.0   
 998         0.0  6.0  5.0  6.0  5.0  7.0  5.0  5.0  6.0  8.0  ...  5.0  6.0   
 999         0.0  6.0  5.0  6.0  5.0  7.0  5.0  5.0  6.0  8.0  ...  5.0  6.0   
 
       95   96   97   98   99  scenari

In [5]:
from models.ema_dam_uncertain1 import dam_uncertain_problem1
from utils.ea.create_models import create_dam_robust_training


robustness_evaluation(model=create_dam_robust_training, problem=dam_uncertain_problem1, 
                      random_seed=1793476144, steps=100, scenarios_num=1000,
                      scenario_path="../results/dam_scenarios/evaluation_scenarios_random_inflow.csv",
                      policy_path='../results/ea_dam_robust/random_inflow_avg_1-13-06-2022-02-49_policy.csv',
                      result_path=f'../results/dam_robust_performance/ea_random_inflow_avg')

[MainProcess/INFO] performing 1000 scenarios * 1 policies * 1 model(s) = 1000 experiments
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.p

(     s_init_idx     0    1    2    3    4     5    6    7    8  ...   93   94  \
 0           0.0  10.0  7.0  5.0  5.0  5.0  10.0  7.0  6.0  6.0  ...  7.0  6.0   
 1           0.0  10.0  7.0  5.0  5.0  5.0  10.0  7.0  6.0  6.0  ...  7.0  6.0   
 2           0.0  10.0  7.0  5.0  5.0  5.0  10.0  7.0  6.0  6.0  ...  7.0  6.0   
 3           0.0  10.0  7.0  5.0  5.0  5.0  10.0  7.0  6.0  6.0  ...  7.0  6.0   
 4           0.0  10.0  7.0  5.0  5.0  5.0  10.0  7.0  6.0  6.0  ...  7.0  6.0   
 ..          ...   ...  ...  ...  ...  ...   ...  ...  ...  ...  ...  ...  ...   
 995         0.0  10.0  7.0  5.0  5.0  5.0  10.0  7.0  6.0  6.0  ...  7.0  6.0   
 996         0.0  10.0  7.0  5.0  5.0  5.0  10.0  7.0  6.0  6.0  ...  7.0  6.0   
 997         0.0  10.0  7.0  5.0  5.0  5.0  10.0  7.0  6.0  6.0  ...  7.0  6.0   
 998         0.0  10.0  7.0  5.0  5.0  5.0  10.0  7.0  6.0  6.0  ...  7.0  6.0   
 999         0.0  10.0  7.0  5.0  5.0  5.0  10.0  7.0  6.0  6.0  ...  7.0  6.0   
 
       95   96

# Robust Dam Problem (deep)

In [3]:
from models.ema_dam_uncertain1 import dam_uncertain_problem1
from utils.ea.create_models import create_dam_deep_training


robustness_evaluation(model=create_dam_deep_training, problem=dam_uncertain_problem1, 
                      random_seed=1793476144, steps=100, scenarios_num=1000,
                      scenario_path="../results/dam_scenarios/evaluation_scenarios.csv",
                      policy_path='../results/ea_dam_deep/20_1-03-07-2022-09-34_policy.csv',
                      result_path=f'../results/dam_deep_performance_3/ea')

[MainProcess/INFO] performing 1000 scenarios * 1 policies * 1 model(s) = 1000 experiments
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.p

(         s_init     0     1     2    3    4    5    6    7    8  ...   93  \
 0    155.321773  10.0  10.0  10.0  7.0  5.0  5.0  6.0  6.0  7.0  ...  7.0   
 1    126.723411  10.0  10.0  10.0  7.0  5.0  5.0  6.0  6.0  7.0  ...  7.0   
 2    136.122819  10.0  10.0  10.0  7.0  5.0  5.0  6.0  6.0  7.0  ...  7.0   
 3    164.708120  10.0  10.0  10.0  7.0  5.0  5.0  6.0  6.0  7.0  ...  7.0   
 4    165.943724  10.0  10.0  10.0  7.0  5.0  5.0  6.0  6.0  7.0  ...  7.0   
 ..          ...   ...   ...   ...  ...  ...  ...  ...  ...  ...  ...  ...   
 995  199.910831  10.0  10.0  10.0  7.0  5.0  5.0  6.0  6.0  7.0  ...  7.0   
 996  131.942802  10.0  10.0  10.0  7.0  5.0  5.0  6.0  6.0  7.0  ...  7.0   
 997  176.601969  10.0  10.0  10.0  7.0  5.0  5.0  6.0  6.0  7.0  ...  7.0   
 998  129.312759  10.0  10.0  10.0  7.0  5.0  5.0  6.0  6.0  7.0  ...  7.0   
 999  159.885022  10.0  10.0  10.0  7.0  5.0  5.0  6.0  6.0  7.0  ...  7.0   
 
       94   95   96   97   98   99  scenario  policy          

In [3]:
from models.ema_dam_uncertain1 import dam_uncertain_problem1
from utils.ea.create_models import create_dam_deep_training


robustness_evaluation(model=create_dam_deep_training, problem=dam_uncertain_problem1, 
                      random_seed=1793476144, steps=100, scenarios_num=1000,
                      scenario_path="../results/dam_scenarios/evaluation_scenarios.csv",
                      policy_path='../results/ea_dam_deep/mv_20_1-03-07-2022-13-04_policy.csv',
                      result_path=f'../results/dam_deep_performance_3/ea_mv')

[MainProcess/INFO] performing 1000 scenarios * 1 policies * 1 model(s) = 1000 experiments
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.p

(         s_init     0     1    2    3    4    5    6     7    8  ...   93  \
 0    155.321773  10.0  10.0  9.0  5.0  5.0  6.0  7.0  10.0  5.0  ...  6.0   
 1    126.723411  10.0  10.0  9.0  5.0  5.0  6.0  7.0  10.0  5.0  ...  6.0   
 2    136.122819  10.0  10.0  9.0  5.0  5.0  6.0  7.0  10.0  5.0  ...  6.0   
 3    164.708120  10.0  10.0  9.0  5.0  5.0  6.0  7.0  10.0  5.0  ...  6.0   
 4    165.943724  10.0  10.0  9.0  5.0  5.0  6.0  7.0  10.0  5.0  ...  6.0   
 ..          ...   ...   ...  ...  ...  ...  ...  ...   ...  ...  ...  ...   
 995  199.910831  10.0  10.0  9.0  5.0  5.0  6.0  7.0  10.0  5.0  ...  6.0   
 996  131.942802  10.0  10.0  9.0  5.0  5.0  6.0  7.0  10.0  5.0  ...  6.0   
 997  176.601969  10.0  10.0  9.0  5.0  5.0  6.0  7.0  10.0  5.0  ...  6.0   
 998  129.312759  10.0  10.0  9.0  5.0  5.0  6.0  7.0  10.0  5.0  ...  6.0   
 999  159.885022  10.0  10.0  9.0  5.0  5.0  6.0  7.0  10.0  5.0  ...  6.0   
 
       94   95   96   97   98   99  scenario  policy          

In [4]:
from models.ema_dam_uncertain1 import dam_uncertain_problem1
from utils.ea.create_models import create_dam_deep_training


robustness_evaluation(model=create_dam_deep_training, problem=dam_uncertain_problem1, 
                      random_seed=1793476144, steps=100, scenarios_num=1000,
                      scenario_path="../results/dam_scenarios/evaluation_scenarios.csv",
                      policy_path='../results/ea_dam_deep/avg_20_1-06-07-2022-06-01_policy.csv',
                      result_path=f'../results/dam_deep_performance_3/ea_avg')

[MainProcess/INFO] performing 1000 scenarios * 1 policies * 1 model(s) = 1000 experiments
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.p

(         s_init     0    1    2    3    4    5    6    7    8  ...   93   94  \
 0    155.321773  10.0  9.0  9.0  5.0  6.0  5.0  6.0  6.0  5.0  ...  5.0  6.0   
 1    126.723411  10.0  9.0  9.0  5.0  6.0  5.0  6.0  6.0  5.0  ...  5.0  6.0   
 2    136.122819  10.0  9.0  9.0  5.0  6.0  5.0  6.0  6.0  5.0  ...  5.0  6.0   
 3    164.708120  10.0  9.0  9.0  5.0  6.0  5.0  6.0  6.0  5.0  ...  5.0  6.0   
 4    165.943724  10.0  9.0  9.0  5.0  6.0  5.0  6.0  6.0  5.0  ...  5.0  6.0   
 ..          ...   ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
 995  199.910831  10.0  9.0  9.0  5.0  6.0  5.0  6.0  6.0  5.0  ...  5.0  6.0   
 996  131.942802  10.0  9.0  9.0  5.0  6.0  5.0  6.0  6.0  5.0  ...  5.0  6.0   
 997  176.601969  10.0  9.0  9.0  5.0  6.0  5.0  6.0  6.0  5.0  ...  5.0  6.0   
 998  129.312759  10.0  9.0  9.0  5.0  6.0  5.0  6.0  6.0  5.0  ...  5.0  6.0   
 999  159.885022  10.0  9.0  9.0  5.0  6.0  5.0  6.0  6.0  5.0  ...  5.0  6.0   
 
       95   96    97   98 

# Robust Dam3 Problem

In [3]:
from models.ema_dam_uncertain import dam_uncertain_problem
from utils.ea.create_models import create_dam3_deep_training


robustness_evaluation(model=create_dam3_deep_training, problem=dam_uncertain_problem, 
                      random_seed=1793476144, steps=100, scenarios_num=1000,
                      scenario_path="../results/dam_scenarios/evaluation_scenarios.csv",
                      policy_path='../results/ea_dam_deep/3_avg_200_1-15-07-2022-06-32_policy.csv',
                      result_path=f'../results/dam3_deep_performance/ea_avg/ea_avg')

[MainProcess/INFO] performing 1000 scenarios * 1 policies * 1 model(s) = 1000 experiments
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.p

(         s_init    0    1    2    3    4    5    6    7    8  ...   93   94  \
 0    155.321773  4.0  5.0  5.0  5.0  5.0  5.0  5.0  5.0  4.0  ...  5.0  4.0   
 1    126.723411  4.0  5.0  5.0  5.0  5.0  5.0  5.0  5.0  4.0  ...  5.0  4.0   
 2    136.122819  4.0  5.0  5.0  5.0  5.0  5.0  5.0  5.0  4.0  ...  5.0  4.0   
 3    164.708120  4.0  5.0  5.0  5.0  5.0  5.0  5.0  5.0  4.0  ...  5.0  4.0   
 4    165.943724  4.0  5.0  5.0  5.0  5.0  5.0  5.0  5.0  4.0  ...  5.0  4.0   
 ..          ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
 995  199.910831  4.0  5.0  5.0  5.0  5.0  5.0  5.0  5.0  4.0  ...  5.0  4.0   
 996  131.942802  4.0  5.0  5.0  5.0  5.0  5.0  5.0  5.0  4.0  ...  5.0  4.0   
 997  176.601969  4.0  5.0  5.0  5.0  5.0  5.0  5.0  5.0  4.0  ...  5.0  4.0   
 998  129.312759  4.0  5.0  5.0  5.0  5.0  5.0  5.0  5.0  4.0  ...  5.0  4.0   
 999  159.885022  4.0  5.0  5.0  5.0  5.0  5.0  5.0  5.0  4.0  ...  5.0  4.0   
 
       95   96   97   98   99  scenari

# Discrete Lake Problem

In [3]:
from models.ema_lake1 import lake_problem1
from utils.ea.create_models import create_lake_discrete_training


evaluation(model=create_lake_discrete_training, problem=lake_problem1, random_seed=1793476144, steps=99,
           policy_path='../results/ea_lake/100_1-27-06-2022-05-33_policy.csv',
           result_path=f'../results/lake_discrete_performance_2/ea')

[MainProcess/INFO] performing 1 scenarios * 1 policies * 1 model(s) = 1 experiments
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
[MainProcess/INFO] performing experiments sequentially
[MainProcess/INFO] 1 cases completed
[Mai

(      0    1    2    3    4    5    6    7    8    9  ...   92   93    94  \
 0  10.0  9.0  6.0  2.0  2.0  5.0  3.0  3.0  5.0  2.0  ...  9.0  5.0  10.0   
 
     95   96    97   98  scenario  policy                model  
 0  6.0  9.0  10.0  9.0      None      67  lakeDiscreteProblem  
 
 [1 rows x 102 columns],
 {'utility': array([0.65090788]), 'reliability': array([0.77777778])})

# Robust Lake Problem

In [5]:
from models.ema_lake_uncertain1 import lake_uncertain_problem1
from utils.ea.create_models import create_lake_deep_training


robustness_evaluation(model=create_lake_deep_training, problem=lake_uncertain_problem1, 
                      random_seed=1793476144, steps=99, scenarios_num=1000,
                      scenario_path="../results/lake_scenarios/evaluation_scenarios.csv",
                      policy_path='../results/ea_lake_robust/100_1-27-06-2022-08-18_policy.csv',
                      result_path=f'../results/lake_robust_performance_2/ea')

[MainProcess/INFO] performing 1000 scenarios * 1 policies * 1 model(s) = 1000 experiments
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.p

(            b     delta      mean         q     stdev     0    1    2    3  \
 0    0.394152  0.988445  0.022462  2.288250  0.001989  10.0  9.0  7.0  7.0   
 1    0.358404  0.980787  0.019681  2.412040  0.001070  10.0  9.0  7.0  7.0   
 2    0.370154  0.973234  0.011586  2.069689  0.001057  10.0  9.0  7.0  7.0   
 3    0.405885  0.977141  0.023722  2.748324  0.001477  10.0  9.0  7.0  7.0   
 4    0.407430  0.982980  0.011083  2.017728  0.001412  10.0  9.0  7.0  7.0   
 ..        ...       ...       ...       ...       ...   ...  ...  ...  ...   
 995  0.449889  0.973243  0.024590  2.406265  0.001783  10.0  9.0  7.0  7.0   
 996  0.364929  0.977669  0.018504  2.553378  0.001336  10.0  9.0  7.0  7.0   
 997  0.420752  0.989461  0.019657  2.423532  0.001715  10.0  9.0  7.0  7.0   
 998  0.361641  0.978747  0.010098  2.244658  0.001657  10.0  9.0  7.0  7.0   
 999  0.399856  0.972723  0.013633  2.311686  0.001066  10.0  9.0  7.0  7.0   
 
        4  ...    92    93   94    95   96   97   

In [3]:
from models.ema_lake_uncertain1 import lake_uncertain_problem1
from utils.ea.create_models import create_lake_deep_training


robustness_evaluation(model=create_lake_deep_training, problem=lake_uncertain_problem1, 
                      random_seed=1793476144, steps=99, scenarios_num=1000,
                      scenario_path="../results/lake_scenarios/evaluation_scenarios.csv",
                      policy_path='../results/ea_lake_robust/100_avg_1-28-06-2022-06-32_policy.csv',
                      result_path=f'../results/lake_robust_performance_2/ea_avg')

[MainProcess/INFO] performing 1000 scenarios * 1 policies * 1 model(s) = 1000 experiments
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.p

(            b     delta      mean         q     stdev     0     1     2    3  \
 0    0.394152  0.988445  0.022462  2.288250  0.001989  10.0  10.0  10.0  6.0   
 1    0.358404  0.980787  0.019681  2.412040  0.001070  10.0  10.0  10.0  6.0   
 2    0.370154  0.973234  0.011586  2.069689  0.001057  10.0  10.0  10.0  6.0   
 3    0.405885  0.977141  0.023722  2.748324  0.001477  10.0  10.0  10.0  6.0   
 4    0.407430  0.982980  0.011083  2.017728  0.001412  10.0  10.0  10.0  6.0   
 ..        ...       ...       ...       ...       ...   ...   ...   ...  ...   
 995  0.449889  0.973243  0.024590  2.406265  0.001783  10.0  10.0  10.0  6.0   
 996  0.364929  0.977669  0.018504  2.553378  0.001336  10.0  10.0  10.0  6.0   
 997  0.420752  0.989461  0.019657  2.423532  0.001715  10.0  10.0  10.0  6.0   
 998  0.361641  0.978747  0.010098  2.244658  0.001657  10.0  10.0  10.0  6.0   
 999  0.399856  0.972723  0.013633  2.311686  0.001066  10.0  10.0  10.0  6.0   
 
        4  ...    92    93

In [7]:
from models.ema_lake_uncertain1 import lake_uncertain_problem1
from utils.ea.create_models import create_lake_deep_training


robustness_evaluation(model=create_lake_deep_training, problem=lake_uncertain_problem1, 
                      random_seed=1793476144, steps=99, scenarios_num=1000,
                      scenario_path="../results/lake_scenarios/evaluation_scenarios.csv",
                      policy_path='../results/ea_lake_robust/mv_100_1-07-07-2022-03-20_policy.csv',
                      result_path=f'../results/lake_robust_performance_2/ea_mv')

[MainProcess/INFO] performing 1000 scenarios * 1 policies * 1 model(s) = 1000 experiments
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.p

(            b     delta      mean         q     stdev     0    1    2    3  \
 0    0.394152  0.988445  0.022462  2.288250  0.001989  10.0  9.0  6.0  0.0   
 1    0.358404  0.980787  0.019681  2.412040  0.001070  10.0  9.0  6.0  0.0   
 2    0.370154  0.973234  0.011586  2.069689  0.001057  10.0  9.0  6.0  0.0   
 3    0.405885  0.977141  0.023722  2.748324  0.001477  10.0  9.0  6.0  0.0   
 4    0.407430  0.982980  0.011083  2.017728  0.001412  10.0  9.0  6.0  0.0   
 ..        ...       ...       ...       ...       ...   ...  ...  ...  ...   
 995  0.449889  0.973243  0.024590  2.406265  0.001783  10.0  9.0  6.0  0.0   
 996  0.364929  0.977669  0.018504  2.553378  0.001336  10.0  9.0  6.0  0.0   
 997  0.420752  0.989461  0.019657  2.423532  0.001715  10.0  9.0  6.0  0.0   
 998  0.361641  0.978747  0.010098  2.244658  0.001657  10.0  9.0  6.0  0.0   
 999  0.399856  0.972723  0.013633  2.311686  0.001066  10.0  9.0  6.0  0.0   
 
        4  ...   92   93   94   95   96   97   98 

# Fishing Problem

In [ ]:
from models.ema_fishing import fishing_problem
from utils.ea.create_models import create_fishing_training


evaluation(model=create_fishing_training, problem=fishing_problem, random_seed=1793476144, steps=200,
           policy_path='../results/ea_fishing/200_1-08-07-2022-07-03_policy.csv',
           result_path=f'../results/fishing_performance/ea', real_num=True)

[MainProcess/INFO] performing 1 scenarios * 1 policies * 1 model(s) = 1 experiments
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df[name] = pd.Series(dtype=dtype)
/Users/zppei/Documents/PhD-Project/code/Evolutionary/EMAWorkbench/em_framework/callbacks.py:191: